# Getting Started

In [ ]:
# This file provides starter code for extracting features from the xml files and
## for doing some learning.
##
## The basic set-up: 
## ----------------
## main() will run code to extract features, learn, and make predictions.
## 
## extract_feats() is called by main(), and it will iterate through the 
## train/test directories and parse each xml file into an xml.etree.ElementTree, 
## which is a standard python object used to represent an xml file in memory.
## (More information about xml.etree.ElementTree objects can be found here:
## http://docs.python.org/2/library/xml.etree.elementtree.html
## and here: http://eli.thegreenplace.net/2012/03/15/processing-xml-in-python-with-elementtree/)
## It will then use a series of "feature-functions" that you will write/modify
## in order to extract dictionaries of features from each ElementTree object.
## Finally, it will produce an N x D sparse design matrix containing the union
## of the features contained in the dictionaries produced by your "feature-functions."
## This matrix can then be plugged into your learning algorithm.
##
## The learning and prediction parts of main() are largely left to you, though
## it does contain code that randomly picks class-specific weights and predicts
## the class with the weights that give the highest score. If your prediction
## algorithm involves class-specific weights, you should, of course, learn 
## these class-specific weights in a more intelligent way.
##
## Feature-functions:
## --------------------
## "feature-functions" are functions that take an ElementTree object representing
## an xml file (which contains, among other things, the sequence of system calls a
## piece of potential malware has made), and returns a dictionary mapping feature names to 
## their respective numeric values. 
## For instance, a simple feature-function might map a system call history to the
## dictionary {'first_call-load_image': 1}. This is a boolean feature indicating
## whether the first system call made by the executable was 'load_image'. 
## Real-valued or count-based features can of course also be defined in this way. 
## Because this feature-function will be run over ElementTree objects for each 
## software execution history instance, we will have the (different)
## feature values of this feature for each history, and these values will make up 
## one of the columns in our final design matrix.
## Of course, multiple features can be defined within a single dictionary, and in
## the end all the dictionaries returned by feature functions (for a particular
## training example) will be unioned, so we can collect all the feature values 
## associated with that particular instance.
##
## Two example feature-functions, first_last_system_call_feats() and 
## system_call_count_feats(), are defined below.
## The first of these functions indicates what the first and last system-calls 
## made by an executable are, and the second records the total number of system
## calls made by an executable.
##
## What you need to do:
## --------------------
## 1. Write new feature-functions (or modify the example feature-functions) to
## extract useful features for this prediction task.
## 2. Implement an algorithm to learn from the design matrix produced, and to
## make predictions on unseen data. Naive code for these two steps is provided
## below, and marked by TODOs.
##
## Computational Caveat
## --------------------
## Because the biggest of any of the xml files is only around 35MB, the code below 
## will parse an entire xml file and store it in memory, compute features, and
## then get rid of it before parsing the next one. Storing the biggest of the files 
## in memory should require at most 200MB or so, which should be no problem for
## reasonably modern laptops. If this is too much, however, you can lower the
## memory requirement by using ElementTree.iterparse(), which does parsing in
## a streaming way. See http://eli.thegreenplace.net/2012/03/15/processing-xml-in-python-with-elementtree/
## for an example. 

In [1]:
import os
from collections import Counter
try:
    import xml.etree.cElementTree as ET
except ImportError:
    import xml.etree.ElementTree as ET
import numpy as np
from scipy import sparse
from sklearn.naive_bayes import MultinomialNB
from sklearn.model_selection import KFold
from sklearn.linear_model import LogisticRegression
from sklearn.linear_model import LogisticRegressionCV
from sklearn.svm import SVC
from sklearn.naive_bayes import MultinomialNB
from sklearn.ensemble import RandomForestClassifier

import tensorflow as tf

import matplotlib.pyplot as plt

import util

In [11]:
# Train directory, test directory, and name of output file for predictions
train_dir = "../malware_data/train"
test_dir = "../malware_data/test"
outputfile = "bag_predictions.csv"

# Feature Extraction

In [2]:
def extract_feats(ffs, direc="train", global_feat_dict=None):
    """
    arguments:
      ffs are a list of feature-functions.
      direc is a directory containing xml files (expected to be train or test).
      global_feat_dict is a dictionary mapping feature_names to column-numbers; it
      should only be provided when extracting features from test data, so that 
      the columns of the test matrix align correctly.

    returns: 
      a sparse design matrix, a dict mapping features to column-numbers,
      a vector of target classes, and a list of system-call-history ids in order 
      of their rows in the design matrix.
      
      Note: the vector of target classes returned will contain the true indices of the
      target classes on the training data, but will contain only -1's on the test
      data
    """
    fds = [] # list of feature dicts
    classes = []
    ids = [] 
    for datafile in os.listdir(direc):
        # extract id and true class (if available) from filename
        id_str,clazz = datafile.split('.')[:2]
        ids.append(id_str)
        # add target class if this is training data
        try:
            classes.append(util.malware_classes.index(clazz))
        except ValueError:
            # we should only fail to find the label in our list of malware classes
            # if this is test data, which always has an "X" label
            assert clazz == "X"
            classes.append(-1)
        rowfd = {}
        # parse file as an xml document
        tree = ET.parse(os.path.join(direc,datafile))
        # accumulate features
        [rowfd.update(ff(tree)) for ff in ffs]
        fds.append(rowfd)
        
    X,feat_dict = make_design_mat(fds,global_feat_dict)
    return X, feat_dict, np.array(classes), ids

In [3]:
def make_design_mat(fds, global_feat_dict=None):
    """
    arguments:
      fds is a list of feature dicts (one for each row).
      global_feat_dict is a dictionary mapping feature_names to column-numbers; it
      should only be provided when extracting features from test data, so that 
      the columns of the test matrix align correctly.
       
    returns: 
        a sparse NxD design matrix, where N == len(fds) and D is the number of
        the union of features defined in any of the fds 
    """
    if global_feat_dict is None:
        all_feats = set()
        [all_feats.update(fd.keys()) for fd in fds]
        feat_dict = dict([(feat, i) for i, feat in enumerate(sorted(all_feats))])
    else:
        feat_dict = global_feat_dict
        
    cols = []
    rows = []
    data = []        
    for i in xrange(len(fds)):
        temp_cols = []
        temp_data = []
        for feat,val in fds[i].iteritems():
            try:
                # update temp_cols iff update temp_data
                temp_cols.append(feat_dict[feat])
                temp_data.append(val)
            except KeyError as ex:
                if global_feat_dict is not None:
                    pass  # new feature in test data; nbd
                else:
                    raise ex

        # all fd's features in the same row
        k = len(temp_cols)
        cols.extend(temp_cols)
        data.extend(temp_data)
        rows.extend([i]*k)

    assert len(cols) == len(rows) and len(rows) == len(data)
   

    X = sparse.csr_matrix((np.array(data),
                   (np.array(rows), np.array(cols))),
                   shape=(len(fds), len(feat_dict)))
    return X, feat_dict

In [4]:
## Here are two example feature-functions. They each take an xml.etree.ElementTree object, 
# (i.e., the result of parsing an xml file) and returns a dictionary mapping 
# feature-names to numeric values.
## TODO: modify these functions, and/or add new ones.
# def first_last_system_call_feats(tree):
#     """
#     arguments:
#       tree is an xml.etree.ElementTree object
#     returns:
#       a dictionary mapping 'first_call-x' to 1 if x was the first system call
#       made, and 'last_call-y' to 1 if y was the last system call made. 
#       (in other words, it returns a dictionary indicating what the first and 
#       last system calls made by an executable were.)
#     """
#     c = Counter()
#     in_all_section = False
#     first = True # is this the first system call
#     last_call = None # keep track of last call we've seen
#     for el in tree.iter():
#         # ignore everything outside the "all_section" element
#         if el.tag == "all_section" and not in_all_section:
#             in_all_section = True
#         elif el.tag == "all_section" and in_all_section:
#             in_all_section = False
#         elif in_all_section:
#             if first:
#                 c["first_call-"+el.tag] = 1
#                 first = False
#             last_call = el.tag  # update last call seen
            
#     # finally, mark last call seen
#     c["last_call-"+last_call] = 1
#     return c

# def system_call_count_feats(tree):
#     """
#     arguments:
#       tree is an xml.etree.ElementTree object
#     returns:
#       a dictionary mapping 'num_system_calls' to the number of system_calls
#       made by an executable (summed over all processes)
#     """
#     c = Counter()
#     in_all_section = False
#     for el in tree.iter():
#         # ignore everything outside the "all_section" element
#         if el.tag == "all_section" and not in_all_section:
#             in_all_section = True
#         elif el.tag == "all_section" and in_all_section:
#             in_all_section = False
#         elif in_all_section:
#             c['num_system_calls'] += 1
#     return c

In [4]:
# Extract features based on name of system calls
def tag_count_feats(tree):
    """
    arguments:
      tree is an xml.etree.ElementTree object
    returns:
      a dictionary mapping el.tag to the number of system_calls
      identified by that tag (summed over all processes)
    """
    c = Counter()
    in_all_section = False
    for el in tree.iter():
        # ignore everything outside the "all_section" element
        if el.tag == "all_section" and not in_all_section:
            in_all_section = True
        elif el.tag == "all_section" and in_all_section:
            in_all_section = False
        elif in_all_section:
            c[el.tag] += 1
    return c

In [18]:
# Selective bag of words
def attribute_feats(tree):
    c = Counter()
    in_all_section = False
    for el in tree.iter():
        # ignore everything outside the "all_section" element
        if el.tag == "all_section" and not in_all_section:
            in_all_section = True
        elif el.tag == "all_section" and in_all_section:
            in_all_section = False
        elif in_all_section:
            # Look at attributes
            print el.attrib
            #c[el.attrib] += 1
    return c

In [6]:
# Extract features based on system call proportions
# def tag_prop_feats(tree):
#     """
#     arguments:
#       tree is an xml.etree.ElementTree object
#     returns:
#       a dictionary mapping el.tag to the number of system_calls
#       identified by that tag (summed over all processes)
#     """
#     c = Counter()
#     in_all_section = False
#     for el in tree.iter():
#         # ignore everything outside the "all_section" element
#         if el.tag == "all_section" and not in_all_section:
#             in_all_section = True
#         elif el.tag == "all_section" and in_all_section:
#             in_all_section = False
#         elif in_all_section:
#             c[el.tag] += 1
#     total = float(sum([c[ind] for ind in c]))
#     for ind in c:
#         c[ind] = c[ind] / total
#     return c

In [ ]:
# List of feature functions defined above
ffs = [tag_count_feats, attribute_feats] #first_last_system_call_feats, system_call_count_feats, 

# extract features
print "extracting training features..."
X_train,global_feat_dict,t_train,train_ids = extract_feats(ffs, train_dir)
print "done extracting training features"

extracting training features...
{'successful': '1', 'end_address': '$415000', 'filename_hash': 'hash_error', 'filename': 'c:\\1025be1934a50c3355adb359507f2862.EX', 'address': '$400000', 'size': '86016'}
{'successful': '1', 'end_address': '$7C9C9000', 'filename_hash': 'e753d19a2e3b98b2b3b8f02f276092096d10f22d', 'filename': 'C:\\WINDOWS\\system32\\ntdll.dll', 'address': '$7C910000', 'size': '757760'}
{'successful': '1', 'end_address': '$7C908000', 'filename_hash': 'c88d57cc99f75cd928b47b6e444231f26670138f', 'filename': 'C:\\WINDOWS\\system32\\kernel32.dll', 'address': '$7C800000', 'size': '1081344'}
{'successful': '1', 'end_address': '$77E4A000', 'filename_hash': 'ea2e9bac1789b53d7efcd675a63f4a2b44898439', 'filename': 'C:\\WINDOWS\\system32\\ADVAPI32.dll', 'address': '$77DA0000', 'size': '696320'}
{'successful': '1', 'end_address': '$77EE2000', 'filename_hash': 'f3bb6474ec18ee9cccc02ef44510a78b42058a41', 'filename': 'C:\\WINDOWS\\system32\\RPCRT4.dll', 'address': '$77E50000', 'size': '59

In [14]:
# get rid of training data and load test data
# del X_train
# del t_train
# del train_ids
print "extracting test features..."
X_test,_,t_ignore,test_ids = extract_feats(ffs, test_dir, global_feat_dict=global_feat_dict)
print "done extracting test features"
print

extracting test features...


NameError: name 'global_feat_dict' is not defined

# Training

In [9]:
# Function for k-fold cross validation
def kfold(k, model, X, Y):
    kf = KFold(n_splits=k)
    accs = []
    for train_fold_index, validate_fold_index in kf.split(X):
        X_train_fold = X[train_fold_index]
        X_validate_fold = X[validate_fold_index]
        Y_train_fold = Y[train_fold_index]
        Y_validate_fold = Y[validate_fold_index]
        model.fit(X_train_fold, Y_train_fold)
        Y_hat = model.predict(X_validate_fold)
        acc = np.mean(Y_hat == Y_validate_fold)
        accs.append(acc)
    return np.mean(accs)

In [12]:
# logistic regression model
print "learning..."
Logreg = LogisticRegression(multi_class="multinomial", solver="lbfgs")
Logreg.fit(X_train, t_train)
print kfold(5, Logreg, X_train, t_train)
print "done learning"

learning...
0.720351109083
done learning


In [10]:
# tune logreg
C_vec = [10. ** a for a in range(-3, 4)]
accs = []
for C in C_vec:
    Logreg = LogisticRegression(C=C, multi_class="multinomial", solver="lbfgs")
    accs.append(kfold(5, Logreg, X_train, t_train))
print (C_vec, accs)

([0.001, 0.01, 0.1, 1.0, 10.0, 100.0, 1000.0], [0.72262172638248545, 0.7171153876414218, 0.71354922293381162, 0.7203511090829936, 0.71063345449586424, 0.72100255437889782, 0.71614084226316921])


In [13]:
# SVM
svc = SVC()
print kfold(5, svc, X_train, t_train)

0.782892480055


In [9]:
svc = SVC(class_weight='balanced')
print kfold(5, svc, X_train, t_train)

0.682754533105


In [17]:
# Naive Bayes
mnb = MultinomialNB(fit_prior=False)
print kfold(5, mnb, X_train, t_train)

0.461850587192


In [19]:
# Random forest
rf = RandomForestClassifier()
print kfold(5, rf, X_train, t_train)

0.884314435126


In [158]:
# Neural network

# Transform data
X = X_train.toarray()

n,m = X.shape
num_labels = 15
d = 50
eta = 0.001
num_epochs = 1000
BATCH_SIZE = 100

# Turn labels into one-hot matrix
Y = np.zeros((n,num_labels))
for i in range(n):
    Y[i,t_train[i]] = 1

# Placeholder for x, y_, and keep_prob
x = tf.placeholder(tf.float32, [None,m])
y_ = tf.placeholder(tf.float32, [None,num_labels])

In [163]:
# Initialize the hidden weights and biases.
W_hidden = tf.Variable(tf.random_uniform((m,d),0,0.5))
b_hidden = tf.Variable(tf.random_uniform((1,d),0,0.5))

# The hidden layer.
hidden = tf.nn.softmax(tf.matmul(x,W_hidden) + b_hidden)

# Initialize the output weights and biases.
W_out = tf.Variable(tf.random_uniform((d,num_labels),0,0.5))
b_out = tf.Variable(tf.random_uniform((1,num_labels),0,0.5))

# The output layer.
y = tf.nn.softmax(tf.matmul(hidden,W_out) + b_out)

# Optimization.
cross_entropy = tf.reduce_mean(-tf.reduce_sum(y_ * tf.log(y), reduction_indices=[1])) # -tf.reduce_sum(y_*tf.log(y))
# train_step = tf.train.AdamOptimizer(eta).minimize(cross_entropy) # BEST
train_step = tf.train.MomentumOptimizer(eta,0.9).minimize(cross_entropy)
# train_step = tf.train.AdagradOptimizer(eta).minimize(cross_entropy)
# train_step = tf.train.GradientDescentOptimizer(eta).minimize(cross_entropy)

# Evaluation.
predicted_class = tf.argmax(y,1)
correct_prediction = tf.equal(tf.argmax(y,1), tf.argmax(y_,1))
accuracy = tf.reduce_mean(tf.cast(correct_prediction, "float"))

In [164]:
# Create a local session to run this computation.
with tf.Session() as s:
    print "initializing..."
    # Run all the initializers to prepare the trainable parameters.
    tf.global_variables_initializer().run()

    print "training..."
    # Iterate and train.
    for step in xrange(num_epochs * n // BATCH_SIZE):
        if step%10000 == 0:
            print "Step #", step
        offset = (step * BATCH_SIZE) % n
        batch_data = X[offset:(offset + BATCH_SIZE), :]
        batch_labels = Y[offset:(offset + BATCH_SIZE)]
        train_step.run(feed_dict={x:batch_data, y_:batch_labels})

    print "Train Accuracy:", accuracy.eval(feed_dict={x:X, y_:Y})
    
    print "making predictions..."
    classification = s.run(tf.argmax(y,1), feed_dict={x:X_test.toarray()})
    print "done making predictions"
    print

    print "writing predictions..."
    util.write_predictions(classification, test_ids, outputfile)
    print "done!"

initializing...
training...
Step # 0
Step # 10000
Step # 20000
Step # 30000
Train Accuracy: 0.732988
making predictions...
done making predictions

writing predictions...
done!
